In [1]:
import sys, os
import pandas as pd

In [44]:
sys.path.append('/media/moraa/New Volume/Ontita/10Academy/Cohort B/Projects/Week1/User_Analytics_in_the_telecommunication_Industry')

from dotenv import load_dotenv
from utils.db_connections import DBConnection
from utils.clean import DataCleaner
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
import numpy as np
from sklearn.metrics.pairwise import euclidean_distances
from sklearn.model_selection import train_test_split
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor
from sklearn.metrics import mean_squared_error

In [3]:
# Create an instance of DBConnection
db_conn = DBConnection()

# Specify the table name you want to read
table_name = 'xdr_data'

# Read data from the specified table into a DataFrame
df = db_conn.read_table_to_dataframe(table_name)

df.head()

Bearer Id            Start  Start ms              End  End ms  \
0  1.311448e+19   4/4/2019 12:01     770.0  4/25/2019 14:35   662.0   
1  1.311448e+19   4/9/2019 13:04     235.0   4/25/2019 8:15   606.0   
2  1.311448e+19   4/9/2019 17:42       1.0  4/25/2019 11:58   652.0   
3  1.311448e+19   4/10/2019 0:31     486.0   4/25/2019 7:36   171.0   
4  1.311448e+19  4/12/2019 20:10     565.0  4/25/2019 10:40   954.0   

   Dur. (ms)          IMSI  MSISDN/Number          IMEI  \
0  1823652.0  2.082014e+14   3.366496e+10  3.552121e+13   
1  1365104.0  2.082019e+14   3.368185e+10  3.579401e+13   
2  1361762.0  2.082003e+14   3.376063e+10  3.528151e+13   
3  1321509.0  2.082014e+14   3.375034e+10  3.535661e+13   
4  1089009.0  2.082014e+14   3.369980e+10  3.540701e+13   

      Last Location Name  ...  Youtube DL (Bytes)  Youtube UL (Bytes)  \
0  9.16456699548519E+015  ...          15854611.0           2501332.0   
1                L77566A  ...          20247395.0          19111729.0   
2                D42335A  ...          19725661.0          14699576.0   
3                T21824A  ...          21388122.0          15146643.0   
4                D88865A  ...          15259380.0          18962873.0   

   Netflix DL (Bytes)  Netflix UL (Bytes)  Gaming DL (Bytes)  \
0           8198936.0           9656251.0        278082303.0   
1          18338413.0          17227132.0        608750074.0   
2          17587794.0           6163408.0        229584621.0   
3          13994646.0           1097942.0        799538153.0   
4          17124581.0            415218.0        527707248.0   

   Gaming UL (Bytes)  Other DL (Bytes)  Other UL (Bytes)  Total UL (Bytes)  \
0         14344150.0       171744450.0         8814393.0        36749741.0   
1          1170709.0       526904238.0        15055145.0        53800391.0   
2           395630.0       410692588.0         4215763.0        27883638.0   
3         10849722.0       749039933.0        12797283.0        43324218.0   
4          3529801.0       550709500.0        13910322.0        38542814.0   

   Total DL (Bytes)  
0       308879636.0  
1       653384965.0  
2       279807335.0  
3       846028530.0  
4       569138589.0  

[5 rows x 55 columns]

In [5]:
# Create an instance of DataCleaner
cleaner = DataCleaner()

# Remove columns with missing values exceeding the threshold
df = cleaner.remove_columns_with_missing_values(df)

# Fill missing values in numerical columns
df = cleaner.fill_missing_values_numerical(df)

# Fill missing values in categorical columns
df = cleaner.fill_missing_values_categorical(df)

Engagement Score to each user

In [7]:
# Separate numerical and non-numerical columns
numerical_cols = df.select_dtypes(include=['number'])
non_numerical_cols = df.select_dtypes(exclude=['number'])

In [8]:
# Aggregate the information per customer
aggregated_info = numerical_cols.groupby(['MSISDN/Number']).agg({
    'TCP DL Retrans. Vol (Bytes)': 'mean',
    'TCP UL Retrans. Vol (Bytes)': 'mean',
    'Avg RTT DL (ms)': 'mean',
    'Avg RTT UL (ms)': 'mean',
    'Avg Bearer TP DL (kbps)': 'mean',
    'Avg Bearer TP UL (kbps)': 'mean'
}).reset_index()

# Drop any rows with missing values
aggregated_info.dropna(inplace=True)

# Select the features for clustering
X = aggregated_info[['TCP DL Retrans. Vol (Bytes)', 'TCP UL Retrans. Vol (Bytes)', 
                     'Avg RTT DL (ms)', 'Avg RTT UL (ms)', 
                     'Avg Bearer TP DL (kbps)', 'Avg Bearer TP UL (kbps)']]

# Perform k-means clustering with k=3
kmeans = KMeans(n_clusters=3, random_state=42)
clusters = kmeans.fit_predict(X)

# Add the cluster labels to the aggregated data
aggregated_info['Cluster'] = clusters

# Analyze the characteristics of each cluster
cluster_characteristics = aggregated_info.groupby('Cluster').mean()

# Print the characteristics of each cluster
print(cluster_characteristics)

         MSISDN/Number  TCP DL Retrans. Vol (Bytes)  \
Cluster                                               
0         4.514731e+10                 1.581571e+07   
1         3.368247e+10                 2.820712e+09   
2         3.368759e+10                 9.898283e+08   

         TCP UL Retrans. Vol (Bytes)  Avg RTT DL (ms)  Avg RTT UL (ms)  \
Cluster                                                                  
0                       7.285051e+05       117.990845        16.726642   
1                       1.067448e+06       104.428839        38.273408   
2                       4.255220e+06       111.621530        40.981688   

         Avg Bearer TP DL (kbps)  Avg Bearer TP UL (kbps)  
Cluster                                                    
0                   11496.744644              1499.290362  
1                   63786.363296              8322.404494  
2                   58084.360465              8411.408527  


In [16]:
# After fitting the KMeans model
kmeans = KMeans(n_clusters=3, random_state=42)
clusters = kmeans.fit_predict(X)  # X is feature matrix used for clustering

# Add the cluster labels to your DataFrame
aggregated_info['Cluster'] = clusters

print(aggregated_info)

        MSISDN/Number  TCP DL Retrans. Vol (Bytes)  \
0        3.360100e+10                 2.080991e+07   
1        3.360100e+10                 2.080991e+07   
2        3.360100e+10                 2.080991e+07   
3        3.360101e+10                 1.066000e+03   
4        3.360101e+10                 1.507977e+07   
...               ...                          ...   
106852   3.379000e+10                 2.080991e+07   
106853   4.188282e+10                 1.655032e+07   
106854   3.197021e+12                 2.080991e+07   
106855   3.370000e+14                 2.080991e+07   
106856   8.823971e+14                 2.080991e+07   

        TCP UL Retrans. Vol (Bytes)  Avg RTT DL (ms)  Avg RTT UL (ms)  \
0                     759658.664811        46.000000         0.000000   
1                     759658.664811        30.000000         1.000000   
2                     759658.664811       109.795706        17.662883   
3                     759658.664811        69.000000       

In [17]:
# Calculate the average engagement score for each cluster
cluster_engagement = aggregated_info.groupby('Cluster')['Engagement Score'].mean()

# Find the cluster with the lowest average engagement score
least_engaged_cluster = cluster_engagement.idxmin()

# Print the cluster with the lowest average engagement score
print("The least engaged cluster is Cluster:", least_engaged_cluster)

The least engaged cluster is Cluster: 0


In [24]:
# Identify the centroid of the least engaged cluster (Cluster 0)
less_engaged_cluster_centroid = cluster_characteristics.loc[0, :].values

# Check the dimensions of the centroid vector
print("Dimensions of less_engaged_cluster_centroid:", less_engaged_cluster_centroid.shape)

# Check the dimensions of the user data matrix X
print("Dimensions of X:", X.shape)

# If the dimensions are different, adjust the centroid vector to match the number of features in X
if less_engaged_cluster_centroid.shape[0] != X.shape[1]:
    # Assuming less_engaged_cluster_centroid has one extra feature (column)
    less_engaged_cluster_centroid = less_engaged_cluster_centroid[:-1]  # Remove the extra feature

# Recalculate the Euclidean distances using the corrected centroid vector
engagement_scores = euclidean_distances(X, [less_engaged_cluster_centroid])

# Add engagement scores to the aggregated_info DataFrame
aggregated_info['Engagement Score'] = engagement_scores.flatten()



Dimensions of less_engaged_cluster_centroid: (7,)
Dimensions of X: (106857, 6)


In [25]:
# Adjust the centroid vector to have the same number of features as X
less_engaged_cluster_centroid = less_engaged_cluster_centroid[:X.shape[1]]

# Recalculate the Euclidean distances using the corrected centroid vector
engagement_scores = euclidean_distances(X, [less_engaged_cluster_centroid])

# Add engagement scores to the aggregated_info DataFrame
aggregated_info['Engagement Score'] = engagement_scores.flatten()


In [28]:
print("Engagement scores:", engagement_scores)


Engagement scores: [[4.51265067e+10]
 [4.51265067e+10]
 [4.51265067e+10]
 ...
 [4.51265067e+10]
 [4.51265067e+10]
 [4.51265067e+10]]


In [29]:
# Iterate over each user and their corresponding engagement score
for idx, (msisdn, score) in enumerate(zip(aggregated_info['MSISDN/Number'], engagement_scores.flatten())):
    print(f"User {msisdn}: Engagement Score = {score}")


User 33601001722.0: Engagement Score = 45126506721.99132
User 33601001754.0: Engagement Score = 45126506721.99158
User 33601002511.0: Engagement Score = 45126506721.99029
User 33601007832.0: Engagement Score = 45147315569.10093
User 33601008617.0: Engagement Score = 45132236988.49424
User 33601010682.0: Engagement Score = 45136910298.54603
User 33601011634.0: Engagement Score = 45136862665.80585
User 33601011959.0: Engagement Score = 45147316357.101105
User 33601014694.0: Engagement Score = 45126506721.99029
User 33601020306.0: Engagement Score = 45126506981.38487
User 33601021045.0: Engagement Score = 45126506721.99168
User 33601021217.0: Engagement Score = 45132728898.39841
User 33601022743.0: Engagement Score = 45126506721.99123
User 33601024291.0: Engagement Score = 45126506721.990295
User 33601025738.0: Engagement Score = 45126506721.99029
User 33601026147.0: Engagement Score = 45147283717.10312
User 33601027208.0: Engagement Score = 45126506721.99175
User 33601031129.0: Engagemen

Experience Score per User

In [30]:
# Calculate the centroid of the worst experience cluster (Cluster with the highest TCP retransmission volume)
worst_experience_cluster_centroid = cluster_characteristics.loc[cluster_characteristics['TCP DL Retrans. Vol (Bytes)'].idxmax()].values[:-1]

# Extract the numerical features for calculating the experience score
X_experience = aggregated_info[['TCP DL Retrans. Vol (Bytes)', 'TCP UL Retrans. Vol (Bytes)', 
                                 'Avg RTT DL (ms)', 'Avg RTT UL (ms)', 
                                 'Avg Bearer TP DL (kbps)', 'Avg Bearer TP UL (kbps)']]

# Calculate the Euclidean distance between each user's data point and the centroid of the worst experience cluster
experience_score = euclidean_distances(X_experience, worst_experience_cluster_centroid.reshape(1, -1))

# Assign the experience score to each user
aggregated_info['Experience Score'] = experience_score

# Display the DataFrame with the experience score assigned to each user
print("Experience Score for Each User:")
print(aggregated_info[['MSISDN/Number', 'Experience Score']])

Experience Score for Each User:
        MSISDN/Number  Experience Score
0        3.360100e+10      3.377957e+10
1        3.360100e+10      3.377957e+10
2        3.360100e+10      3.377957e+10
3        3.360101e+10      3.380031e+10
4        3.360101e+10      3.378531e+10
...               ...               ...
106852   3.379000e+10      3.377957e+10
106853   4.188282e+10      3.378384e+10
106854   3.197021e+12      3.377957e+10
106855   3.370000e+14      3.377957e+10
106856   8.823971e+14      3.377957e+10

[106857 rows x 2 columns]


Average of engagement and experience scores

In [31]:
# Combine MSISDN/Number and engagement scores into a list of tuples
user_engagement = list(zip(aggregated_info['MSISDN/Number'], engagement_scores.flatten()))

# Sort users based on their engagement scores
sorted_users = sorted(user_engagement, key=lambda x: x[1], reverse=True)

# Print the top ten users and their engagement scores
print("Top Ten Users by Engagement Score:")
for idx, (msisdn, score) in enumerate(sorted_users[:10], start=1):
    print(f"{idx}. User {msisdn}: Engagement Score = {score}")

Top Ten Users by Engagement Score:
1. User 33763588772.0: Engagement Score = 45203989164.8633
2. User 33669054076.0: Engagement Score = 45158750151.42092
3. User 33661679531.0: Engagement Score = 45153912268.81041
4. User 33664710587.0: Engagement Score = 45147372261.45997
5. User 33761544858.0: Engagement Score = 45147316890.366776
6. User 33669328368.0: Engagement Score = 45147316888.97393
7. User 33763605685.0: Engagement Score = 45147316886.72941
8. User 33664535559.0: Engagement Score = 45147316885.27585
9. User 33763938125.0: Engagement Score = 45147316881.238914
10. User 33668872978.0: Engagement Score = 45147316876.045616


In [32]:
# Calculate the centroid of the worst experience cluster (Cluster with the highest TCP retransmission volume)
worst_experience_cluster_centroid = cluster_characteristics.loc[cluster_characteristics['TCP DL Retrans. Vol (Bytes)'].idxmax()].values[:-1]

# Extract the numerical features for calculating the experience score
X_experience = aggregated_info[['TCP DL Retrans. Vol (Bytes)', 'TCP UL Retrans. Vol (Bytes)', 
                                 'Avg RTT DL (ms)', 'Avg RTT UL (ms)', 
                                 'Avg Bearer TP DL (kbps)', 'Avg Bearer TP UL (kbps)']]

# Calculate the Euclidean distance between each user's data point and the centroid of the worst experience cluster
experience_score = euclidean_distances(X_experience, worst_experience_cluster_centroid.reshape(1, -1))

# Assign the experience score to each user
aggregated_info['Experience Score'] = experience_score

# Sort users based on their experience scores
sorted_users = aggregated_info.sort_values(by='Experience Score', ascending=True)

# Print the top ten users and their experience scores
print("Top Ten Users by Experience Score:")
print(sorted_users[['MSISDN/Number', 'Experience Score']].head(10))


Top Ten Users by Experience Score:
       MSISDN/Number  Experience Score
85785   3.369858e+10      2.952687e+10
32273   3.365871e+10      2.952943e+10
58026   3.366491e+10      2.954896e+10
31942   3.365863e+10      2.956270e+10
62049   3.366613e+10      2.960595e+10
70079   3.366877e+10      2.965035e+10
43629   3.366131e+10      2.968508e+10
48341   3.366240e+10      2.969897e+10
64113   3.366682e+10      2.984797e+10
98211   3.376264e+10      3.002980e+10


In [43]:
# Combine MSISDN/Number, engagement scores, and experience scores into a list of tuples
user_scores = list(zip(aggregated_info['MSISDN/Number'], engagement_scores.flatten(), aggregated_info['Experience Score']))

# Calculate satisfaction scores as the average of engagement and experience scores
satisfaction_scores = [(msisdn, (engagement_score + experience_score) / 2) for msisdn, engagement_score, experience_score in user_scores]

# Sort users based on their satisfaction scores
sorted_users_satisfaction = sorted(satisfaction_scores, key=lambda x: x[1], reverse=True)

# Print the top ten satisfied users and their satisfaction scores
print("Top Ten Satisfied Users:")
for idx, (msisdn, score) in enumerate(sorted_users_satisfaction[:10], start=1):
    print(f"{idx}. User {msisdn}: Satisfaction Score = {score}")


Top Ten Satisfied Users:
1. User 33763605685.0: Satisfaction Score = 39473844900.84483
2. User 33762062356.0: Satisfaction Score = 39473844878.99592
3. User 33621240336.0: Satisfaction Score = 39473844873.41186
4. User 33616407285.0: Satisfaction Score = 39473844871.6093
5. User 33650128412.0: Satisfaction Score = 39473844867.903656
6. User 33626353776.0: Satisfaction Score = 39473844866.37177
7. User 33761544858.0: Satisfaction Score = 39473844861.511475
8. User 33686581755.0: Satisfaction Score = 39473844860.75718
9. User 33699042279.0: Satisfaction Score = 39473844857.34591
10. User 33607833304.0: Satisfaction Score = 39473844855.44804


Building a regression Model

In [48]:
# Extract the first element of each tuple in satisfaction_scores
y = np.array([score[0] for score in satisfaction_scores])

# Prepare the feature matrix (X)
X = aggregated_info[['TCP DL Retrans. Vol (Bytes)', 'TCP UL Retrans. Vol (Bytes)', 
                     'Avg RTT DL (ms)', 'Avg RTT UL (ms)', 
                     'Avg Bearer TP DL (kbps)', 'Avg Bearer TP UL (kbps)']]

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Initialize and train Gradient Boosting Regressor
gb_regressor = GradientBoostingRegressor(n_estimators=100, learning_rate=0.1, max_depth=5, random_state=42)
gb_regressor.fit(X_train, y_train)
# Make predictions
gb_y_pred = gb_regressor.predict(X_test)

# Initialize and train Random Forest Regressor
rf_regressor = RandomForestRegressor(n_estimators=100, max_depth=5, random_state=42)
rf_regressor.fit(X_train, y_train)
# Make predictions
rf_y_pred = rf_regressor.predict(X_test)

# Evaluate models
gb_mse = mean_squared_error(y_test, gb_y_pred)
rf_mse = mean_squared_error(y_test, rf_y_pred)

print("Mean Squared Error (Gradient Boosting):", gb_mse)
print("Mean Squared Error (Random Forest):", rf_mse)



Mean Squared Error (Gradient Boosting): 3.0105481644411505e+23
Mean Squared Error (Random Forest): 2.9582560306717065e+23
